# Dora Hacks Challenge 
## Team 3, Stage 1 Implementing a QRNG on IBM QPUs


In [1]:
# Quantum Random Number Generator

In [1]:
import numpy as np
import matplotlib.pyplot as plt

from qiskit import QuantumCircuit, transpile, qiskit
from qiskit_aer import AerSimulator
from qiskit_ibm_runtime import QiskitRuntimeService
from qiskit.quantum_info import SparsePauliOp
from qiskit.transpiler.preset_passmanagers import generate_preset_pass_manager
from qiskit.visualization.counts_visualization import plot_histogram

In [2]:
# Building an 'n' qubit quantum circuit with all qubits in equal superposition using hadamard gate
def get_qc_for_n_qubits_superpos(n):
    qc = QuantumCircuit(n)
    for qbit in range(n):
        qc.h(qbit)
    return qc

# Number of Qubits 
n = 100

qc = get_qc_for_n_qubits_superpos(n)
qc.measure_all()

# Display Circuit
qc.draw()

┌───┐ ░ ┌─┐                                                         »
     q_0: ┤ H ├─░─┤M├─────────────────────────────────────────────────────────»
          ├───┤ ░ └╥┘┌─┐                                                      »
     q_1: ┤ H ├─░──╫─┤M├──────────────────────────────────────────────────────»
          ├───┤ ░  ║ └╥┘┌─┐                                                   »
     q_2: ┤ H ├─░──╫──╫─┤M├───────────────────────────────────────────────────»
          ├───┤ ░  ║  ║ └╥┘┌─┐                                                »
     q_3: ┤ H ├─░──╫──╫──╫─┤M├────────────────────────────────────────────────»
          ├───┤ ░  ║  ║  ║ └╥┘┌─┐                                             »
     q_4: ┤ H ├─░──╫──╫──╫──╫─┤M├─────────────────────────────────────────────»
          ├───┤ ░  ║  ║  ║  ║ └╥┘┌─┐                                          »
     q_5: ┤ H ├─░──╫──╫──╫──╫──╫─┤M├──────────────────────────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║ └╥┘┌─┐                                       »
     q_6: ┤ H ├─░──╫──╫──╫──╫──╫──╫─┤M├───────────────────────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║ └╥┘┌─┐                                    »
     q_7: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫─┤M├────────────────────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐                                 »
     q_8: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫─┤M├─────────────────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐                              »
     q_9: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├──────────────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐                           »
    q_10: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├───────────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐                        »
    q_11: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├────────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐                     »
    q_12: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├─────────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐                  »
    q_13: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├──────────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐               »
    q_14: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├───────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐            »
    q_15: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├────────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐         »
    q_16: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├─────────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐      »
    q_17: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├──────»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐   »
    q_18: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├───»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘┌─┐»
    q_19: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─┤M├»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ └╥┘»
    q_20: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ »
    q_21: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ »
    q_22: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ »
    q_23: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─»
          ├───┤ ░  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║  ║ »
    q_24: ┤ H ├─░──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫──╫─»
          

# IBM Quantum Simulator Implementation

In [ ]:
simulator = AerSimulator()
compiled_circuit = transpile(qc, simulator)
sim_result = simulator.run(compiled_circuit, shots = 100, memory = True).result()
counts = sim_result.get_counts ()
print("Simulation Results:", counts)

In [ ]:
# Create a legend for the histogram
legend = ['QRNG']

# Plotting the histogram
plt.figure(figsize=(10, 6))  # Set figure size
plot_histogram([counts], legend=legend, color=['crimson'], title="QRNG Simulation")
plt.show()  # Show the plot

# IBM Quantum Machine Implementation - IBM Runtime Protocols v0.30.0

In [8]:
# Connecting to IBM Service
 
# service = QiskitRuntimeService(channel="ibm_quantum", token="<MY_IBM_QUANTUM_TOKEN>")
service = QiskitRuntimeService(channel="ibm_quantum", token="70592aeff7ab936235667ce5e59f0204f8587a6ce5c54383b95f55e0fc27dcb5d091b98a61ba72758795375c56c0dbe1dd8f3e9cceb842f821da8b9fbde2e109")
backend = service.least_busy(simulator=False, operational=True)

In [10]:
# Convert to an ISA circuit - Transpose
pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuit = pm.run(qc)
isa_circuit.draw('mpl', idle_wires=False)

In [11]:
# Execute
# Construct the Estimator instance.
from qiskit_ibm_runtime import Sampler

#Running the job 
sampler = Sampler(mode=backend)
job = sampler.run([isa_circuit], shots = 100)

# Use the job ID to retrieve your job data later
print(f">>> Job ID: {job.job_id()}")

>>> Job ID: cw53w48qg250008cvx1g


In [12]:
pub_result = job.result()

results = qiskit.primitives.PrimitiveResult(pub_result)

for result in results:
    data_bin = result.data
    meas = data_bin.meas
    counts = meas.get_counts()
    raw_data = meas.get_bitstrings()
    
print(results)
print(f"\nRandom Numbers Generated:\n {raw_data}")
print(f"\nCount of Random Numbers:\n {counts}")
   

PrimitiveResult([PubResult(data=DataBin(meas=BitArray(<shape=(), num_shots=100, num_bits=100>)), metadata={'circuit_metadata': {}})], metadata={})

Random Numbers Generated:
 ['0111011010110000000111001101011100100110010100100010111010100111111001010011010100000011001011001110', '0001010011011100000000100000001110110101010111110010010101100000000010001100111100010011100111110111', '1100010001010001011000100011100001111001010110000000110000001111100110000111010100100001101100111001', '1111100000101011001010101111110000001011110111011000001100011000111101000010001111110000010011111101', '1101101000100111000010111010001001110110011100101110001011111111010100110010000101011100011111010011', '0111111000111010110110101111100110110100100010001110001001000001011000111110111001001110000000111110', '0111110101111101001001110000110100011100010100000111001111000000110110010001101001010101100001011100', '11100011010011000101000010110010110101000001100011101110111111001010111100010111110000010111011

## Visualize Output

In [13]:
# Create a legend for the histogram
legend = ['QRNG']

# Plotting the histogram
plt.figure(figsize=(10, 6))  # Set figure size
plot_histogram([counts], legend=legend, color=['crimson'], title="QRNG")
plt.show()  # Show the plot

<Figure size 1000x600 with 0 Axes>

In [14]:
# Write output data to external File 
def output_QRNG(data, file_path):
    with open(file_path, 'a') as file:
        for output in data:
            file.write(output + ', ')
    file.close()

output_QRNG(raw_data, 'QRNG_IBM_runtime_output.txt')
output_QRNG(counts, 'QRNG_IBM_runtime_counts.txt')

# Alternative IBM Quantum Machine Implementation - Using IBM qBraid Protocols v0.8.3

In [15]:
from qbraid.runtime.ibm import QiskitJob
from qbraid.runtime.ibm import QiskitRuntimeProvider

In [16]:
# Set API_Key to your IBM API Key 
API_KEY = "70592aeff7ab936235667ce5e59f0204f8587a6ce5c54383b95f55e0fc27dcb5d091b98a61ba72758795375c56c0dbe1dd8f3e9cceb842f821da8b9fbde2e109"
provider = QiskitRuntimeService(channel='ibm_quantum', token=API_KEY)
backend = provider.least_busy(simulator=False, operational=True)
qbraid_provider = QiskitRuntimeProvider(token=API_KEY, channel='ibm_quantum' )
qbraid_provider.get_devices()

[<qbraid.runtime.ibm.device.QiskitBackend('ibm_brisbane')>,
 <qbraid.runtime.ibm.device.QiskitBackend('ibm_kyiv')>,
 <qbraid.runtime.ibm.device.QiskitBackend('ibm_sherbrooke')>]

In [18]:
# Convert to an ISA circuit and layout-mapped observables.
pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuit = pm.run(qc)
isa_circuit.draw('mpl', idle_wires=False)

In [19]:
# Submit Job through an specific quantum device 

# Select a quantum device from the list of gte_devices() output 
quantum_device = 'ibm_brisbane'
device = qbraid_provider.get_device(quantum_device)
shot_count = 100
job = device.run(isa_circuit, shots=shot_count, memory=True)
print(f">>> Job ID: ", job.id)

>>> Job ID:  cw53xx76f0t0008728k0


In [20]:
# Collect result and print them
job_id = job.id
job = provider.job(job_id)
QBraidJob = QiskitJob(job_id, job )
result = QBraidJob.result()

raw_data = result.data.measurements    
print(raw_data)

[[1 1 1 ... 1 0 0]
 [1 1 1 ... 1 1 1]
 [0 0 1 ... 1 0 0]
 ...
 [1 0 0 ... 0 0 0]
 [0 0 1 ... 1 0 0]
 [0 1 0 ... 1 0 1]]


In [ ]:
# Write output data to external File 

with open('QRNG_IBM_qBraid_output.txt', 'a') as file:
        for output in raw_data:
            file.write(str(output) + '\n')
file.close()